In [ ]:
# get markers?

In [2]:
library(SingleCellExperiment)
library(dplyr)
library(MetaMarkers)
library(Seurat)

In [3]:
exp0 = read.delim('GSE106118_UMI_count_merge.txt', sep = '\t')
mtd = read.delim('cui_cluster_anno.csv', sep = ',')
rownames(mtd) = unlist(mtd[,1])

In [4]:
genes = unlist(exp0[,1])
exp1 <- as.matrix(exp0[,-1])
rownames(exp1) = genes
exp1[1:2,1:3]

HE5W_1_LA.1 HE5W_1_LA.2 HE5W_1_LA.3
A1BG     0           0           0          
A1BG-AS1 0           0           0

In [5]:
mtd[1:2,]

Cell.Name   Cluster
HE5W_1_LA.1 HE5W_1_LA.1 C2 (CM)
HE5W_1_LA.3 HE5W_1_LA.3 C2 (CM)

In [6]:
# subset to 3,842 cells with anno
ids = match(mtd[,1], colnames(exp1))

In [9]:
# create seurat object
seu = CreateSeuratObject(counts = exp1[,ids], meta.data = mtd)
seu

Warning message:
“Feature names cannot have underscores ('_'), replacing with dashes ('-')”
Warning message:
“Data is of class matrix. Coercing to dgCMatrix.”


An object of class Seurat 
24153 features across 3842 samples within 1 assay 
Active assay: RNA (24153 features, 0 variable features)
 1 layer present: counts

In [10]:
# save
saveRDS(seu, file = 'Cui_data.rds')

In [7]:
# get SCE object
sce2 = SingleCellExperiment(list(counts = exp1[,ids]))
colData(sce2) = DataFrame(mtd)
assay(sce2, "cpm") = convert_to_cpm(assay(sce2))

In [18]:
# get cell type markers on whole data
markers = compute_markers(assay(sce2, "cpm"), cell_type_labels = sce2$Cluster)
head(markers)

group cell_type gene  fold_change auroc     log_fdr   population_size
1 all   C1 (5W)   KRT19 14.264328   0.9560007 -296.2083 257            
2 all   C1 (5W)   KRT8  11.890145   0.9503161 -288.8496 257            
3 all   C1 (5W)   TNNT1 30.577023   0.9427896 -279.2151 257            
4 all   C1 (5W)   PGAM4 20.479351   0.9289712 -262.0001 257            
5 all   C1 (5W)   KRT18  9.663127   0.9171727 -247.7312 257            
6 all   C1 (5W)   DMKN   6.699384   0.9152055 -245.3815 257            
  population_fraction average_expression se_expression detection_rate
1 0.06689224           619.64916          41.350968    0.9805447     
2 0.06689224          2994.62369         193.153075    0.9922179     
3 0.06689224           614.79356          52.998792    0.9610895     
4 0.06689224            73.15376           3.376526    0.8910506     
5 0.06689224          2779.74138         210.995027    0.9961089     
6 0.06689224           323.54329          17.062199    0.9844358     
  fold_change_detection precision recall   
1  5.177922             0.2715517 0.9805447
2  1.790563             0.1138393 0.9922179
3  5.384283             0.2794118 0.9610895
4 11.237421             0.4490196 0.8910506
5  1.704167             0.1089362 0.9961089
6  2.932784             0.1740028 0.9844358

In [20]:
head(markers[markers$cell_type=='C2 (CM)',])

group cell_type gene  fold_change auroc     log_fdr    population_size
1 all   C2 (CM)   MYL7  8.933738    0.9396700 -1050.6673 1492           
2 all   C2 (CM)   TNNT2 7.251713    0.9316651 -1013.1598 1492           
3 all   C2 (CM)   TPM1  6.138333    0.9215374  -966.2397 1492           
4 all   C2 (CM)   TNNC1 7.316055    0.9203833  -961.2056 1492           
5 all   C2 (CM)   ACTC1 7.380610    0.9189781  -954.9687 1492           
6 all   C2 (CM)   MYL4  6.680951    0.9106956  -917.5140 1492           
  population_fraction average_expression se_expression detection_rate
1 0.3883394           28387.301          472.30836     0.9959786     
2 0.3883394            7984.051          119.58201     0.9939678     
3 0.3883394           12714.651          191.41382     0.9979893     
4 0.3883394            8437.818          137.94764     0.9899464     
5 0.3883394           11663.159          204.25767     0.9892761     
6 0.3883394            5198.728           91.96861     0.9852547     
  fold_change_detection precision recall   
1 1.213089              0.4351391 0.9959786
2 1.298733              0.4519963 0.9939678
3 1.041838              0.3981283 0.9979893
4 1.253114              0.4431443 0.9899464
5 1.283342              0.4490417 0.9892761
6 1.356688              0.4628463 0.9852547

In [21]:
# save marker list
export_meta_markers(markers, "Cui_celltype_markers.csv", names(markers))